# 0 - Quick Imports

In [1]:
# set path to the parent dir
import os
import sys
sys.path.append('src')
os.chdir(os.path.join(os.path.expanduser('~'),'project/r2e-edits-internal'))

!pwd

/home/naman/project/r2e-edits-internal


In [2]:
import numpy as np
from collections import deque
import pandas as pd
import os,sys

import sys 
# sys.path.append(".")
# sys.path.append("..")

import random
# from torchvision import transforms, utils
from PIL import Image, ImageFilter 

import PIL
from PIL import Image
import numpy as np

# matplotlib
import matplotlib.pyplot as plt
%matplotlib inline
%config InlineBackend.figure_format='retina'

# seaborn
# import seaborn as sns
# sns.set()

# Some more magic so that the notebook will reload external python modules;
# see http://stackoverflow.com/questions/1907993/autoreload-of-modules-in-ipython
%load_ext autoreload
%autoreload 2

In [3]:
def display_alongside_batch(img_list, resize_dims=(512,512)):
    if isinstance(resize_dims, int):
        resize_dims = (resize_dims,resize_dims)
    res = np.concatenate([np.array(img.resize(resize_dims)) for img in img_list], axis=1)
    return Image.fromarray(res)

In [4]:
from IPython.core.magic import register_cell_magic
from IPython.display import Markdown

@register_cell_magic
def info(line, cell):
    display(Markdown(f'<div class="alert alert-info"><strong>Info!</strong> {cell}</div>'))

@register_cell_magic
def warning(line, cell):
    display(Markdown(f'<div class="alert alert-warning"><strong>Warning!</strong> {cell}</div>'))

@register_cell_magic
def error(line, cell):
    display(Markdown(f'<div class="alert alert-danger"><strong>Error!</strong> {cell}</div>'))

from IPython.display import Markdown

def create_alert_block(alert_type, content):
    html = f'<div class="alert alert-{alert_type}"><strong>{alert_type.capitalize()}!</strong> {content}</div>'
    display(Markdown(html))

In [5]:
from src.r2e_edits.agenthub.utils.log import get_logger
logger = get_logger(name='jupyter')
logger.info('hello')

[05/06/25 07:08:44] INFO     hello

# 1 - Qwen3  Inference

## 1.1 - OpenAI Server

In [8]:
# using openai server - w/o thinking specs
from openai import OpenAI
# Set OpenAI's API key and API base to use SGLang's API server.
openai_api_key = "EMPTY"
openai_api_base = "http://localhost:8000/v1"

client = OpenAI(
    api_key=openai_api_key,
    base_url=openai_api_base,
)

response = client.chat.completions.create(
    model="Qwen/Qwen3-32B",
    messages=[
        {"role": "user", "content": "Give me a short introduction to large language models."},
    ],
    temperature=0.6,
    top_p=0.95,
    # top_k=20,
    max_tokens=32768,
)
print("Chat response:", response)

Chat response: ChatCompletion(id='b94126dc0d1444eaa05ccd6a1209216a', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content=None, refusal=None, role='assistant', audio=None, function_call=None, tool_calls=None, reasoning_content="I'll give you a short and clear introduction to large language models. Here's a concise overview:\n\n**Introduction to Large Language Models:**\n\nLarge Language Models (LLMs) are advanced artificial intelligence systems designed to understand and generate human-like text. They are trained on vast amounts of text data from the internet, books, and other written sources, enabling them to learn patterns, grammar, and context across many languages and topics.\n\nKey characteristics of LLMs include:\n1. **Massive Scale**: They contain billions of parameters (adjustable values) that allow them to process and understand complex patterns in language.\n2. **Versatility**: They can perform a wide range of tasks like translat

In [20]:
logger.info(response.choices[0].message.reasoning_content)
logger.info(response.choices[0].message.content)

[04/29/25 02:43:08] INFO     Okay, the user wants a short introduction to large language models. Let me start by   
                             defining what they are. They're AI systems that process and generate human-like text, 
                             right? I should mention their training data—probably massive text datasets. Then, the 
                             key components: neural networks, especially transformers. Oh, and the architecture    
                             with attention mechanisms.                                                            
                                                                                                                   
                             I need to explain their capabilities: text generation, translation, answering         
                             questions. Maybe give examples of applications like chatbots or content creation.     
                             Also, touch on how they work—predicting the next word based on context. But I should  
                             keep it simple, avoid jargon.                                                         
                                                                                                                   
                             Wait, the user might be someone new to AI, so I should clarify terms like             
                             "transformers" and "attention mechanisms." Maybe compare it to how humans process     
                             language. Also, mention that they can have limitations, like factual accuracy or      
                             biases. But since it's an introduction, maybe keep the focus on the basics and        
                             applications.                                                                         
                                                                                                                   
                             Let me structure it: definition, how they work (training, architecture), what they can
                             do, and some uses. Keep it concise, each part a short paragraph. Avoid technical      
                             details but make sure the core concepts are clear. Check if I need to mention specific
                             models like GPT or BERT, but maybe just refer to them as examples without going into  
                             specifics. Alright, that should cover a good short intro without overwhelming the     
                             user.                                                                                 
                    

                    INFO     Large language models (LLMs) are advanced artificial intelligence systems designed to 
                             understand, generate, and interact with human language. Trained on vast amounts of    
                             text data from books, websites, and other sources, they learn patterns, grammar, and  
                             context to produce coherent and contextually relevant responses. Built using neural   
                             networks—particularly transformer architectures—LLMs employ attention mechanisms to   
                             dynamically focus on key parts of input text, enabling them to handle complex tasks   
                             like answering questions, writing stories, translating languages, or coding. While    
                             powerful, they have limitations, such as occasional inaccuracies or biases inherited  
                             from training data. LLMs power tools like chatbots, virtual assistants, and           
                             content-generation platforms, reshaping how we interact with technology and           
                             information.

In [11]:
# using openai server - with thinking
from openai import OpenAI
# Set OpenAI's API key and API base to use SGLang's API server.
openai_api_key = "EMPTY"
openai_api_base = "http://localhost:8000/v1"

client = OpenAI(
    api_key=openai_api_key,
    base_url=openai_api_base,
)

model = "/home/naman/project/qwen3/LLaMA-Factory/saves/qwen3-32b_end2end_sonnet_combined_maxstep40_sft-exitreason-agent-32k_bz8_epoch2_lr1en5-v1"
# model = "Qwen/Qwen3-32B"
response = client.chat.completions.create(
    model=model,
    messages=[
        {"role": "user", "content": "can you play chess 1. e4 e5 -> 2. d4 "},
    ],
    temperature=0.7,
    top_p=0.8,
    # top_k=20,
    presence_penalty=1.5,
    # max_tokens=32768,
    extra_body={"chat_template_kwargs": {"enable_thinking": True}},
)
print("Chat response:", response)

Chat response: ChatCompletion(id='280c54cca01d418ba6b00f12b4f4a639', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content=None, refusal=None, role='assistant', audio=None, function_call=None, tool_calls=None, reasoning_content="I can help you analyze and play through chess moves. Let's see the position after:\n\n1. e4 e5  \n2. d4\n\nThis is a classic opening sequence that leads to the **Scotch Game** or **Scotch Opening**, where White advances the d-pawn to attack Black's e5 pawn. Now it's Black's turn to respond.\n\nThe most common responses are:\n\n1. **2... exd4** - Capturing the pawn, leading to an open game\n2. **2... Nc6** - Developing the knight and preparing to recapture with ...Nxe5 if needed\n3. **2... d6** - A more solid approach, supporting the e5 pawn\n\nLet me know how you'd like to continue, and I'll help analyze the best moves and strategies! Would you like to try one of these options?\n\nFor example:\n- If you choose 2... 

In [12]:
logger.info(response.choices[0].message.reasoning_content)
logger.info(response.choices[0].message.content)

[05/02/25 03:05:02] INFO     I can help you analyze and play through chess moves. Let's see the position after:    
                                                                                                                   
                             1. e4 e5                                                                              
                             2. d4                                                                                 
                                                                                                                   
                             This is a classic opening sequence that leads to the **Scotch Game** or **Scotch      
                             Opening**, where White advances the d-pawn to attack Black's e5 pawn. Now it's Black's
                             turn to respond.                                                                      
                                                                                                                   
                             The most common responses are:                                                        
                                                                                                                   
                             1. **2... exd4** - Capturing the pawn, leading to an open game                        
                             2. **2... Nc6** - Developing the knight and preparing to recapture with ...Nxe5 if    
                             needed                                                                                
                             3. **2... d6** - A more solid approach, supporting the e5 pawn                        
                                                                                                                   
                             Let me know how you'd like to continue, and I'll help analyze the best moves and      
                             strategies! Would you like to try one of these options?                               
                                                                                                                   
                             For example:                                                                          
                             - If you choose 2... exd4, we'll look at the Scotch Game continuation                 
                             - If you choose 2... Nc6, we'll explore the Classical variation                       
                             - If you choose 2... d6, we'll examine the Modern Scotch line                         
                                                                                                                   
                             Let me know your choice! ♟️                                                            
                                                                                                                   
                                                                                                                   
                                                                                                                   
                             Let's go with **2... exd4** to explore the **Scotch Game** continuation. This is a    
                             dynamic and popular choice that leads to sharp tactical play. After:                  
                                                                                                                   
                             1. e4 e5                                                                              
                             2. d4 exd4                                                                            
                                                                                                                   
                             White has several strong r

                    INFO     None

In [14]:
# using openai server - w/o thinking 
from openai import OpenAI
# Set OpenAI's API key and API base to use SGLang's API server.
openai_api_key = "EMPTY"
openai_api_base = "http://localhost:8000/v1"
model = "/home/naman/project/qwen3/LLaMA-Factory/saves/qwen3-32b_end2end_sonnet_combined_maxstep40_sft-exitreason-agent-32k_bz8_epoch2_lr1en5-v1"
model = "Qwen/Qwen3-32B"

client = OpenAI(
    api_key=openai_api_key,
    base_url=openai_api_base,
)

response = client.chat.completions.create(
    model=model,
    messages=[
        {"role": "user", "content": "Give me a short introduction to large language models."},
    ],
    temperature=0.7,
    top_p=0.8,
    # top_k=20,
    presence_penalty=1.5,
    # max_tokens=32768,
    extra_body={"chat_template_kwargs": {"enable_thinking": False}},
)
print("Chat response:", response)

Chat response: ChatCompletion(id='f805f1193ea24cc381b1f71ea49964e1', choices=[Choice(finish_reason='stop', index=0, logprobs=None, message=ChatCompletionMessage(content='Large Language Models (LLMs) are advanced artificial intelligence systems designed to understand and generate human-like text. They are trained on vast amounts of data from the internet, books, and other sources, allowing them to learn patterns, grammar, and context in multiple languages. LLMs can perform a wide range of tasks, such as answering questions, writing stories, coding, translating languages, and even engaging in conversations.\n\nThese models use deep learning techniques, particularly transformer architectures, which enable them to process input efficiently and maintain context over long stretches of text. While they are powerful tools, they also have limitations, such as potential biases in their training data and occasional inaccuracies. As the field continues to evolve, LLMs are becoming increasingly imp

In [26]:
logger.info(response.choices[0].message.reasoning_content)
logger.info(response.choices[0].message.content)

[04/29/25 02:46:32] INFO     None

                    INFO     Large language models (LLMs) are advanced artificial intelligence systems designed to 
                             understand and generate human-like text. They are trained on vast amounts of data from
                             the internet, books, articles, and other written materials, allowing them to learn    
                             patterns, grammar, and context in natural language. LLMs can perform a wide range of  
                             tasks, such as answering questions, writing stories, coding, translating languages,   
                             and more—often with minimal input or instructions.                                    
                                                                                                                   
                             These models are typically based on deep learning architectures like transformers,    
                             which enable them to process and generate text efficiently and effectively. Popular   
                             examples include GPT (Generative Pre-trained Transformer), BERT, and others developed 
                             by companies like Google, Meta, and Alibaba. While powerful, LLMs also have           
                             limitations, such as potential biases, inaccuracies, and ethical concerns that        
                             researchers continue to address.

## 1.2 - LiteLLM

In [15]:
# using openai server - w/o thinking 
from openai import OpenAI
import litellm

# Set OpenAI's API key and API base to use SGLang's API server.
openai_api_key = "EMPTY"
openai_api_base = "http://localhost:8000/v1"
model = "openai/Qwen/Qwen3-32B"
model = "openai//home/naman/project/qwen3/LLaMA-Factory/saves/qwen3-32b_end2end_sonnet_combined_maxstep40_sft-exitreason-agent-32k_bz8_epoch2_lr1en5-v1"

messages=[
        {"role": "user", "content": "Give me a short introduction to large language models."},
    ]
response = litellm.completion(
                    model=model,
                    messages=messages,
                    # timeout=self.llm_timeout,
                    api_key=openai_api_key,
                    api_base=openai_api_base,
                    temperature=0.7,
                    # top_p=0.8,
                    # top_k=20,
                    # presence_penalty=1.5,
                    # extra_body={"chat_template_kwargs": {"enable_thinking": True}},
                )

# response = litellm.completion(
#                     model="Qwen/Qwen3-32B",
#                     messages=messages,
#                     timeout=self.llm_timeout,
#                     # api_key=None,
#                     temperature=temperature,
#                     api_base=self.llm_base_url,
                    
#                     # max_tokens=3000,
#                     **kwargs,
#                 )


/home/naman/project/r2e-edits-internal/.venv/lib/python3.12/site-packages/pydantic/_internal/_config.py:341: UserWarning: Valid config keys have changed in V2:
* 'fields' has been removed
  warnings.warn(message, UserWarning)


In [16]:
# using openai server - w/o thinking 
from openai import OpenAI
import litellm

# Set OpenAI's API key and API base to use SGLang's API server.
openai_api_key = "EMPTY"
openai_api_base = "http://localhost:8000/v1"
model = "openai/Qwen/Qwen3-32B"
model = "openai//home/naman/project/qwen3/LLaMA-Factory/saves/qwen3-32b_end2end_sonnet_combined_maxstep40_sft-exitreason-agent-32k_bz8_epoch2_lr1en5-v1"

messages=[
        {"role": "user", "content": "Give me a short introduction to large language models."},
    ]
response = litellm.completion(
                    model=model,
                    messages=messages,
                    # timeout=self.llm_timeout,
                    api_key=openai_api_key,
                    api_base=openai_api_base,
                    temperature=0.7,
                    top_p=0.8,
                    top_k=20,
                    presence_penalty=1.5,
                    extra_body={"chat_template_kwargs": {"enable_thinking": True}},
                )
response

ModelResponse(id='e5e4d266b2234437aabbf3266b5ac5ab', created=1746155282, model='/home/naman/project/qwen3/LLaMA-Factory/saves/qwen3-32b_end2end_sonnet_combined_maxstep40_sft-exitreason-agent-32k_bz8_epoch2_lr1en5-v1', object='chat.completion', system_fingerprint=None, choices=[Choices(finish_reason='stop', index=0, message=Message(content=None, role='assistant', tool_calls=None, function_call=None))], usage=Usage(completion_tokens=211, prompt_tokens=18, total_tokens=229, completion_tokens_details=None, prompt_tokens_details=None), service_tier=None)

In [17]:
response = litellm.completion(
                    model=model,
                    messages=messages,
                    # timeout=self.llm_timeout,
                    api_key=openai_api_key,
                    api_base=openai_api_base,
                    temperature=0.7,
                    top_p=0.8,
                    top_k=20,
                    presence_penalty=1.5,
                    extra_body={"chat_template_kwargs": {"enable_thinking": False}},
                )

In [18]:
# logger.info(response.choices[0].message.reasoning_content)
logger.info(response.choices[0].message.content)

[05/02/25 03:08:27] INFO     Large language models (LLMs) are advanced artificial intelligence systems designed to 
                             understand, generate, and respond to human language. They are trained on vast amounts 
                             of text data from diverse sources, allowing them to learn patterns, grammar, context, 
                             and even reasoning capabilities. LLMs can perform a wide range of tasks, such as      
                             answering questions, writing stories, coding, translating languages, and more—often   
                             with minimal instruction.                                                             
                                                                                                                   
                             These models use deep learning techniques, particularly transformer architectures,    
                             which enable efficient processing of sequential data like text. Their ability to      
                             handle complex language tasks has made them valuable tools in research, business,     
                             education, and everyday applications. However, they also raise important              
                             considerations around ethics, bias, privacy, and responsible use.

# 2 -  SWE-smith analysis

In [7]:
from datasets import load_dataset
df = load_dataset('SWE-bench/SWE-smith-trajectories')

In [8]:
df

DatasetDict({
    train: Dataset({
        features: ['messages', 'instance_id'],
        num_rows: 5016
    })
})

In [9]:
# visualize the first traj
for entry in df['train']['messages'][0]:
    logger.info(entry['role'])
    logger.info(entry['content'])

[05/06/25 07:09:56] INFO     system

                    INFO     You are a helpful assistant that can interact with a computer to solve tasks.         
                             <IMPORTANT>                                                                           
                             * If user provides a path, you should NOT assume it's relative to the current working 
                             directory. Instead, you should explore the file system to find the file before working
                             on it.                                                                                
                             </IMPORTANT>                                                                          
                                                                                                                   
                             You have access to the following functions:                                           
                                                                                                                   
                             ---- BEGIN FUNCTION #1: bash ----                                                     
                             Description: Execute a bash command in the terminal.                                  
                                                                                                                   
                             Parameters:                                                                           
                               (1) command (string, required): The bash command to execute. Can be empty to view   
                             additional logs when previous exit code is `-1`. Can be `ctrl+c` to interrupt the     
                             currently running process.                                                            
                             ---- END FUNCTION #1 ----                                                             
                                                                                                                   
                             ---- BEGIN FUNCTION #2: submit ----                                                   
                             Description: Finish the interaction when the task is complete OR if the assistant     
                             cannot proceed further with the task.                                                 
                             No parameters are required for this function.                                         
                             ---- END FUNCTION #2 ----                                                             
                                                                                                                   
                             ---- BEGIN FUNCTION #3: str_replace_editor ----                                       
                             Description: Custom editing tool for viewing, creating and editing files              
                             * State is persistent across command calls and discussions with the user              
                             * If `path` is a file, `view` displays the result of applying `cat -n`. If `path` is a
                             directory, `view` lists non-hidden files and directories up to 2 levels deep          
                             * The `create` command cannot be used if the specified `path` already exists as a file
                             * If a `command` generates a long output, it will be truncated and marked with        
                             `<response clipped>`                                                                  
                             * The `undo_edit` command will revert the last edit made to the file at `path`        
                                                                                                                   
                             Notes for using the `str_re

                    INFO     user

                    INFO     <uploaded_files>                                                                      
                             /testbed                                                                              
                             </uploaded_files>                                                                     
                             I've uploaded a python code repository in the directory /testbed. Consider the        
                             following PR description:                                                             
                                                                                                                   
                             <pr_description>                                                                      
                             [bug] replace_in_file has inconsistent return value                                   
                             ### Describe the bug                                                                  
                                                                                                                   
                             Not really a bug, but a minor inconsistence: `files.replace_in_file` in non-strict    
                             mode return `False` if the pattern was not found, but nothing (e.g. `None`) if it was 
                             found and replaced. Noticed this because I wanted to check the return value.          
                                                                                                                   
                             Trivial change, will make a PR in a minute.                                           
                                                                                                                   
                             ### How to reproduce it                                                               
                                                                                                                   
                             _No response_                                                                         
                                                                                                                   
                             </pr_description>                                                                     
                                                                                                                   
                             Can you help me implement the necessary changes to the repository so that the         
                             requirements specified in the <pr_description> are met?                               
                             I've already taken care of all changes to any of the test files described in the      
                             <pr_description>. This means you DON'T have to modify the testing logic or any of the 
                             tests in any way!                                                                     
                             Your task is to make the minimal changes to non-tests files in the /testbed directory 
                             to ensure the <pr_description> is satisfied.                                          
                             Follow these steps to resolve the issue:                                              
                             1. As a first step, it might be a good idea to find and read code relevant to the     
                             <pr_description>                                                                      
                             2. Create a script to reproduce the error and execute it with `python <filename.py>`  
                             using the bash tool, to confirm the error                                             
                             3. Edit the sourcecode of t

                    INFO     assistant

...

                    INFO     Now let's run the reproduction script again to verify the fix:                        
                                                                                                                   
                             <function=bash>                                                                       
                             <parameter=command>cd /testbed && python reproduce.py</parameter>                     
                             </function>

                    INFO     user

                    INFO     OBSERVATION:                                                                          
                             WARNING: replace_in_file didn't find pattern 'Pattern' in 'test.txt' file.            
                             Pattern not found result: False                                                       
                             Pattern found result: True

                    INFO     assistant

                    INFO     Perfect! The function now has consistent return values:                               
                             - Returns `True` when the pattern is found and replaced                               
                             - Returns `False` when the pattern is not found (in non-strict mode)                  
                             - Raises an exception when the pattern is not found (in strict mode)                  
                                                                                                                   
                             Let's think about edge cases:                                                         
                                                                                                                   
                             1. Empty file:                                                                        
                                - The current implementation will work correctly - if the search pattern isn't     
                             found in an empty file, it will return False (non-strict) or raise exception (strict) 
                                                                                                                   
                             2. Empty search pattern:                                                              
                                - The current implementation will work correctly - an empty search pattern will    
                             match at the start of the file, so it will return True and replace it                 
                                                                                                                   
                             3. Empty replace pattern:                                                             
                                - The current implementation will work correctly - it will effectively delete the  
                             search pattern and return True                                                        
                                                                                                                   
                             4. Binary files:                                                                      
                                - The function takes an encoding parameter defaulting to utf-8, so binary files    
                             should be handled by specifying a different encoding if needed                        
                                                                                                                   
                             5. File doesn't exist:                                                                
                                - The current implementation will raise a FileNotFoundError when trying to load the
                             file, which is appropriate behavior                                                   
                                                                                                                   
                             6. File permissions:                                                                  
                                - If the file is not readable/writable, appropriate OS-level exceptions will be    
                             raised, which is fine                                                                 
                                                                                                                   
                             The implementation handles all these edge cases appropriately, so no additional       
                             changes are needed.                                                                   
                                                                                                                   
                             Let me submit the changes: 

In [10]:
df = load_dataset("R2E-Gym/R2EGym-SFT-Trajectories")

# visualize the first traj
for entry in df['train']['messages'][0]:
    logger.info(entry['role'])
    logger.info(entry['content'])

[05/06/25 07:11:34] INFO     system

                    INFO     You are a programming agent who is provided a github issue and repository bash        
                             environment and is tasked to solve certain tasks (e.g., file localization, testcase   
                             generation, code repair and editing etc) to resolve the issue.                        
                                                                                                                   
                             We have access to the following functions:                                            
                                                                                                                   
                             –– BEGIN FUNCTION #1: file_editor ––                                                  
                             Description:                                                                          
                             Custom editing tool for viewing, creating and editing files                           
                               •     State is persistent across command calls and discussions with the user        
                               •     If path is a file, view displays the result of applying cat -n. If path is a  
                             directory, view lists non-hidden files and directories up to 2 levels deep            
                               •     The create command cannot be used if the specified path already exists as a   
                             file                                                                                  
                               •     If a command generates a long output, it will be truncated and marked with    
                             <response clipped>                                                                    
                               •     The undo_edit command will revert the last edit made to the file at path      
                                                                                                                   
                             Notes for using the str_replace command:                                              
                               •     The old_str parameter should match EXACTLY one or more consecutive lines from 
                             the original file. Be mindful of whitespaces!                                         
                               •     If the old_str parameter is not unique in the file, the replacement will not  
                             be performed. Make sure to include enough context in old_str to make it unique        
                               •     The new_str parameter should contain the edited lines that should replace the 
                             old_str                                                                               
                                                                                                                   
                             Parameters:                                                                           
                               1.    command (string, required)                                                    
                             Allowed values: [view, create, str_replace, insert, undo_edit]                        
                             The command to run.                                                                   
                               2.    path (string, required)                                                       
                             Absolute path to file or directory, e.g. /testbed/file.py or /testbed.                
                               3.    file_text (string, optional)                                                  
                             Required for the create command. Contains the content of the file to be created.      
                               4.    old_str (string, op

                    INFO     user

                    INFO     Consider the following github issue:                                                  
                             <github_issue>                                                                        
                                                                                                                   
                             **Title:** LocalCache raises TypeError when no limit is set                           
                                                                                                                   
                             **Description:**                                                                      
                             When initializing `LocalCache` without specifying a limit, adding items results in a  
                             `TypeError`. This occurs because the cache attempts to compare its length with        
                             `self.limit`, which is `None`.                                                        
                                                                                                                   
                             **Example Code:**                                                                     
                             ```python                                                                             
                             cache = LocalCache()                                                                  
                             cache['a'] = 1                                                                        
                             cache['b'] = 2                                                                        
                             cache['c'] = 3  # This line raises TypeError                                          
                             ```                                                                                   
                                                                                                                   
                             **Expected Behavior:**                                                                
                             `LocalCache` should allow adding items without enforcing a limit when no limit is set,
                             allowing the cache to grow indefinitely without errors.                               
                                                                                                                   
                             **Actual Behavior:**                                                                  
                             A `TypeError` is raised with the message: `'>' not supported between instances of     
                             'int' and 'NoneType'`                                                                 
                                                                                                                   
                                                                                                                   
                             </github_issue>                                                                       
                                                                                                                   
                             Can you help me implement the necessary changes to the repository to fix the          
                             <github_issue>?                                                                       
                             I've already taken care of all changes to any of the test files described in the      
                             <github_issue>. This means you DON'T have to modify the testing logic or any of the   
                             tests in any way!                                                                     
                             Your task is to make the mi

                    INFO     assistant

...

                    INFO     Let's run the updated reproduction script to verify the fix:                          
                                                                                                                   
                             <function=execute_bash>                                                               
                               <parameter=cmd>python /testbed/reproduce_issue.py</parameter>                       
                             </function>

                    INFO     user

                    INFO     Execution output of [execute_bash]:                                                   
                             Test 1: Testing with no limit...                                                      
                             Success: Added items without error                                                    
                             Cache contents: {'a': 1, 'b': 2, 'c': 3}                                              
                                                                                                                   
                             Test 2: Testing with limit=2...                                                       
                             Cache contents: {'b': 2, 'c': 3}                                                      
                             Success: Limit enforced correctly                                                     
                    

                    INFO     assistant

                    INFO     Perfect! Our fix has resolved the issue and we've verified that:                      
                             1. The cache now works correctly when no limit is set (allows unlimited items)        
                             2. The cache still properly enforces limits when they are set                         
                             3. The original TypeError is resolved                                                 
                             4. Edge cases are handled:                                                            
                                - No limit case (works)                                                            
                                - With limit case (works)                                                          
                                - Ordering is preserved (it's an OrderedDict subclass)                             
                                - Limit enforcement removes oldest items first (verified in test 2)                
                                                                                                                   
                             The fix is minimal and maintains the original functionality while adding the ability  
                             to have an unlimited cache when no limit is specified. This matches the expected      
                             behavior described in the issue.                                                      
                                                                                                                   
                             Should I submit this as the solution?                                                 
                                                                                                                   
                             <function=finish>                                                                     
                               <parameter=command>submit</parameter>                                               
                               <parameter=result>Fixed LocalCache TypeError when no limit is set by adding a check 
                             for None limit in __setitem__ method. The fix:                                        
                             1. Allows unlimited items when no limit is set                                        
                             2. Maintains existing limit functionality when a limit is specified                   
                             3. Preserves OrderedDict behavior                                                     
                             4. Handles edge cases properly                                                        
                                                                                                                   
                             Changes made:                                                                         
                             1. Modified __setitem__ in LocalCache to check if limit is None before enforcing it   
                             2. Verified fix with comprehensive test cases                                         
                             3. Confirmed both unlimited and limited cache scenarios work as expected</parameter>  
                             </function>

In [14]:
from datasets import load_dataset, DatasetDict

# 1. Load both train splits
ds1 = load_dataset("r2e-edits/SWE-smith-trajectories-R2E", split="train")
ds2 = load_dataset("R2E-Gym/R2EGym-SFT-Trajectories",     split="train")

# 2. Grab the new system prompt from ds2’s first example
new_system = ds2["messages"][0][0]["content"]

# 3. Mapper to swap in the new system prompt
def replace_system(example):
    msgs = example["messages"].copy()
    msgs[0] = {
        **msgs[0],         # keep role & other keys
        "content": new_system
    }
    return {"messages": msgs}

# 4. Apply to ds1
ds1_updated = ds1.map(replace_system)

# 5. Wrap as a DatasetDict with only a 'train' split
from datasets import DatasetDict
new_ds = DatasetDict({"train": ds1_updated})

# 6. Quick sanity check
print("New system prompt:", new_ds["train"][0]["messages"][0]["content"])

# 7. Push to Hugging Face (make sure you're `huggingface-cli login`ed)
# new_ds.push_to_hub("your-username/SWE-smith-trajectories-R2E-with-new-system")

Map:   0%|          | 0/5016 [00:00<?, ? examples/s]

New system prompt: You are a programming agent who is provided a github issue and repository bash environment and is tasked to solve certain tasks (e.g., file localization, testcase generation, code repair and editing etc) to resolve the issue.

We have access to the following functions:

–– BEGIN FUNCTION #1: file_editor ––
Description:
Custom editing tool for viewing, creating and editing files
  •	State is persistent across command calls and discussions with the user
  •	If path is a file, view displays the result of applying cat -n. If path is a directory, view lists non-hidden files and directories up to 2 levels deep
  •	The create command cannot be used if the specified path already exists as a file
  •	If a command generates a long output, it will be truncated and marked with <response clipped>
  •	The undo_edit command will revert the last edit made to the file at path

Notes for using the str_replace command:
  •	The old_str parameter should match EXACTLY one or more consecut

In [15]:
new_ds

DatasetDict({
    train: Dataset({
        features: ['messages', 'instance_id'],
        num_rows: 5016
    })
})

In [17]:
# visualize the first traj
for entry in new_ds['train']['messages'][100]:
    logger.info(entry['role'])
    logger.info(entry['content'])

[05/06/25 07:20:03] INFO     system

                    INFO     You are a programming agent who is provided a github issue and repository bash        
                             environment and is tasked to solve certain tasks (e.g., file localization, testcase   
                             generation, code repair and editing etc) to resolve the issue.                        
                                                                                                                   
                             We have access to the following functions:                                            
                                                                                                                   
                             –– BEGIN FUNCTION #1: file_editor ––                                                  
                             Description:                                                                          
                             Custom editing tool for viewing, creating and editing files                           
                               •     State is persistent across command calls and discussions with the user        
                               •     If path is a file, view displays the result of applying cat -n. If path is a  
                             directory, view lists non-hidden files and directories up to 2 levels deep            
                               •     The create command cannot be used if the specified path already exists as a   
                             file                                                                                  
                               •     If a command generates a long output, it will be truncated and marked with    
                             <response clipped>                                                                    
                               •     The undo_edit command will revert the last edit made to the file at path      
                                                                                                                   
                             Notes for using the str_replace command:                                              
                               •     The old_str parameter should match EXACTLY one or more consecutive lines from 
                             the original file. Be mindful of whitespaces!                                         
                               •     If the old_str parameter is not unique in the file, the replacement will not  
                             be performed. Make sure to include enough context in old_str to make it unique        
                               •     The new_str parameter should contain the edited lines that should replace the 
                             old_str                                                                               
                                                                                                                   
                             Parameters:                                                                           
                               1.    command (string, required)                                                    
                             Allowed values: [view, create, str_replace, insert, undo_edit]                        
                             The command to run.                                                                   
                               2.    path (string, required)                                                       
                             Absolute path to file or directory, e.g. /testbed/file.py or /testbed.                
                               3.    file_text (string, optional)                                                  
                             Required for the create command. Contains the content of the file to be created.      
                               4.    old_str (string, op

                    INFO     user

                    INFO     <uploaded_files>                                                                      
                             /testbed                                                                              
                             </uploaded_files>                                                                     
                             I've uploaded a python code repository in the directory /testbed. Consider the        
                             following PR description:                                                             
                                                                                                                   
                             <pr_description>                                                                      
                             server: Overwriting a binary object in S3 causes `/moto-api/data.json` to fail        
                             - **Moto version:** 759f26c6d (git cloned)                                            
                             - **Python version:** 3.11.4                                                          
                             - **OS:** macOS 13.4                                                                  
                                                                                                                   
                             After storing a binary file in S3 on the server and overwriting it, the server's      
                             dashboard fails to load due to an unhandled exception while fetching                  
                             `/moto-api/data.json`.                                                                
                                                                                                                   
                             ## Steps to reproduce                                                                 
                                                                                                                   
                             1. Start moto server                                                                  
                                                                                                                   
                                ```shell                                                                           
                                $ python -m moto.server                                                            
                                WARNING: This is a development server. Do not use it in a production deployment.   
                             Use a production WSGI server instead.                                                 
                                 * Running on http://127.0.0.1:5000                                                
                                Press CTRL+C to quit                                                               
                                ```                                                                                
                                                                                                                   
                             1. In another terminal, create an S3 bucket:                                          
                                                                                                                   
                                ```shell                                                                           
                                $ aws --endpoint-url http://localhost:5000/ s3 mb s3://bucket                      
                                make_bucket: bucket                                                                
                                ```                                                                                
                                                        

                    INFO     assistant

...

                    INFO     Let me remove the reproduction script:                                                
                                                                                                                   
                             <function=execute_bash>                                                               
                               <parameter=cmd>cd /testbed && rm reproduce.py</parameter>                           
                             </function>

                    INFO     user

                    INFO     Your command ran successfully and did not produce any output.

                    INFO     assistant

                    INFO     Let's submit again:                                                                   
                                                                                                                   
                             <function=finish>                                                                     
                               <parameter=command>submit</parameter>                                               
                             </function>

In [18]:
new_ds.push_to_hub("r2e-edits/SWE-smith-trajectories-R2E-v2")

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/6 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/r2e-edits/SWE-smith-trajectories-R2E-v2/commit/7f9ae1ba60a0466df5a15918d36c7ff1caaad4e9', commit_message='Upload dataset', commit_description='', oid='7f9ae1ba60a0466df5a15918d36c7ff1caaad4e9', pr_url=None, repo_url=RepoUrl('https://huggingface.co/datasets/r2e-edits/SWE-smith-trajectories-R2E-v2', endpoint='https://huggingface.co', repo_type='dataset', repo_id='r2e-edits/SWE-smith-trajectories-R2E-v2'), pr_revision=None, pr_num=None)

In [ ]:
def convert_trajectory(traj):
    # directly

In [9]:
len(df['train']['messages'][0])

19

In [10]:
for x in df['train']['messages'][0]:
    print (x['role'])
    if x['role'] == 'assistant':
        logger.info(x['content'])

system
user
assistant


[05/05/25 01:02:13] INFO     I'll help you implement the necessary changes to fix the inconsistent return value in 
                             `files.replace_in_file`. Let's follow the steps:                                      
                                                                                                                   
                             1. First, let's find and read the relevant code:                                      
                                                                                                                   
                             <function=bash>                                                                       
                             <parameter=command>find /testbed -type f -name "*.py" | grep -v "test_"</parameter>   
                             </function>

user
assistant


                    INFO     Let me search for files containing "replace_in_file":                                 
                                                                                                                   
                             <function=bash>                                                                       
                             <parameter=command>find /testbed -type f -name "*.py" -exec grep -l "replace_in_file" 
                             {} \;</parameter>                                                                     
                             </function>

user
assistant


...

                    INFO     The reproduction confirms the issue - when the pattern is not found, it returns       
                             `False`, but when the pattern is found and replaced, it returns `None`. This is       
                             inconsistent behavior.                                                                
                                                                                                                   
                             Let's fix this by making it return `True` when the pattern is found and replaced:     
                                                                                                                   
                             <function=str_replace_editor>                                                         
                             <parameter=command>str_replace</parameter>                                            
                             <parameter=path>/testbed/conan/tools/files/files.py</parameter>                       
                             <parameter=old_str>                                                                   
                                 content = content.replace(search, replace)                                        
                                 save(conanfile, file_path, content, encoding=encoding)                            
                             </parameter>                                                                          
                             <parameter=new_str>                                                                   
                                 content = content.replace(search, replace)                                        
                                 save(conanfile, file_path, content, encoding=encoding)                            
                                 return True                                                                       
                             </parameter>                                                                          
                             </function>

user
assistant


                    INFO     Now let's run the reproduction script again to verify the fix:                        
                                                                                                                   
                             <function=bash>                                                                       
                             <parameter=command>cd /testbed && python reproduce.py</parameter>                     
                             </function>

user
assistant


                    INFO     Perfect! The function now has consistent return values:                               
                             - Returns `True` when the pattern is found and replaced                               
                             - Returns `False` when the pattern is not found (in non-strict mode)                  
                             - Raises an exception when the pattern is not found (in strict mode)                  
                                                                                                                   
                             Let's think about edge cases:                                                         
                                                                                                                   
                             1. Empty file:                                                                        
                                - The current implementation will work correctly - if the search pattern isn't     
                             found in an empty file, it will return False (non-strict) or raise exception (strict) 
                                                                                                                   
                             2. Empty search pattern:                                                              
                                - The current implementation will work correctly - an empty search pattern will    
                             match at the start of the file, so it will return True and replace it                 
                                                                                                                   
                             3. Empty replace pattern:                                                             
                                - The current implementation will work correctly - it will effectively delete the  
                             search pattern and return True                                                        
                                                                                                                   
                             4. Binary files:                                                                      
                                - The function takes an encoding parameter defaulting to utf-8, so binary files    
                             should be handled by specifying a different encoding if needed                        
                                                                                                                   
                             5. File doesn't exist:                                                                
                                - The current implementation will raise a FileNotFoundError when trying to load the
                             file, which is appropriate behavior                                                   
                                                                                                                   
                             6. File permissions:                                                                  
                                - If the file is not readable/writable, appropriate OS-level exceptions will be    
                             raised, which is fine                                                                 
                                                                                                                   
                             The implementation handles all these edge cases appropriately, so no additional       
                             changes are needed.                                                                   
                                                                                                                   
                             Let me submit the changes: 

In [11]:
import re
from datasets import load_dataset

# Load the dataset
dataset = load_dataset("SWE-bench/SWE-smith-trajectories")

# Regex to match <function=something_here>
pattern = re.compile(r"<function=([^>]+)>")

all_functions = set()

for row in dataset["train"]:
    for msg in row["messages"]:
        # Only check assistant responses (or remove this check if you want all roles)
        if msg["role"] == "assistant":
            matches = pattern.findall(msg["content"])
            all_functions.update(matches)

print(all_functions)

{'submit', 'bash', 'str_replace_editor'}


In [12]:
import re
from datasets import load_dataset

# Load the dataset
dataset = load_dataset("R2E-Gym/R2EGym-SFT-Trajectories")

# Regex to match <function=something_here>
pattern = re.compile(r"<function=([^>]+)>")

all_functions = set()

for row in dataset["train"]:
    for msg in row["messages"]:
        # Only check assistant responses (or remove this check if you want all roles)
        if msg["role"] == "assistant":
            matches = pattern.findall(msg["content"])
            all_functions.update(matches)

print(all_functions)

{'finish', 'file_editor', 'execute_bash', 'search'}


In [34]:
import re
import logging
from datasets import load_dataset

# # Setup logger (if you already have a logger, skip this part)
# logger = logging.getLogger(__name__)
# logger.setLevel(logging.INFO)
# handler = logging.StreamHandler()
# logger.addHandler(handler)

def extract_function_blocks(dataset, function_name, max_samples=5):
    """
    Finds up to `max_samples` blocks of <function=function_name> ... </function>
    from the assistant messages in a dataset split.
    
    Returns a list of extracted blocks (strings).
    """
    # Regex to capture the entire block for <function=function_name>.*?</function>
    # using DOTALL so we can capture over multiple lines
    pattern = re.compile(rf"<function={function_name}>(.*?)</function>", re.DOTALL)

    extracted = []
    for row in dataset:
        for msg in row["messages"]:
            if msg["role"] == "assistant":
                blocks = pattern.findall(msg["content"])
                for block in blocks:
                    extracted.append(block.strip())
                    if len(extracted) >= max_samples:
                        return extracted
    return extracted

# Load the two datasets
dataset1 = load_dataset("SWE-bench/SWE-smith-trajectories")["train"]
dataset2 = load_dataset("R2E-Gym/R2EGym-SFT-Trajectories")["train"]

# Each entry is (function_in_dataset1, function_in_dataset2)
pairs_to_compare = [
    ("submit", "finish"),
    ("bash", "execute_bash"),
    ("str_replace_editor", "file_editor")
]

# For each pair, extract up to 5 function blocks from each dataset
for fn1, fn2 in pairs_to_compare:
    blocks1 = extract_function_blocks(dataset1, fn1, max_samples=5)
    blocks2 = extract_function_blocks(dataset2, fn2, max_samples=5)

    # Print out side-by-side or sequential comparisons
    logger.info(f"=== Comparing '{fn1}' (dataset1) vs '{fn2}' (dataset2) ===")
    max_len = max(len(blocks1), len(blocks2))
    for i in range(max_len):
        block1 = blocks1[i] if i < len(blocks1) else "[No more samples]"
        block2 = blocks2[i] if i < len(blocks2) else "[No more samples]"
        
        logger.info(f"--- Sample #{i+1} ---")
        logger.info(f"[Dataset1: <function={fn1}>]\n{block1}\n")
        logger.info(f"[Dataset2: <function={fn2}>]\n{block2}\n")
    logger.info("=======================================\n")

[05/04/25 08:14:43] INFO     === Comparing 'submit' (dataset1) vs 'finish' (dataset2) ===

                    INFO     --- Sample #1 ---

                    INFO     [Dataset1: <function=submit>]                                                         
                                                                                                                   
                    

                    INFO     [Dataset2: <function=finish>]                                                         
                             <parameter=command>submit</parameter>                                                 
                               <parameter=result>Fixed LocalCache TypeError when no limit is set by adding a check 
                             for None limit in __setitem__ method. The fix:                                        
                             1. Allows unlimited items when no limit is set                                        
                             2. Maintains existing limit functionality when a limit is specified                   
                             3. Preserves OrderedDict behavior                                                     
                             4. Handles edge cases properly                                                        
                                                                                                                   
                             Changes made:                                                                         
                             1. Modified __setitem__ in LocalCache to check if limit is None before enforcing it   
                             2. Verified fix with comprehensive test cases                                         
                             3. Confirmed both unlimited and limited cache scenarios work as expected</parameter>  
                    

                    INFO     --- Sample #2 ---

...

                    INFO     [Dataset2: <function=file_editor>]                                                    
                             <parameter=command>str_replace</parameter>                                            
                               <parameter=path>/testbed/reproduce_issue.py</parameter>                             
                               <parameter=old_str>def main():                                                      
                                 start_time = time.time()                                                          
                                                                                                                   
                                 try:                                                                              
                                     # Test case 1: Reproducing the error                                          
                                     print("Test 1: Reproducing error with no limit...")                           
                                     cache = LocalCache()                                                          
                                     cache['a'] = 1                                                                
                                     cache['b'] = 2                                                                
                                     cache['c'] = 3                                                                
                                     print("ERROR: Test 1 should have raised TypeError!")                          
                                 except TypeError as e:                                                            
                                     print("Success: Got expected TypeError:", str(e))                             
                                                                                                                   
                                 # Add timeout check                                                               
                                 if time.time() - start_time > 20:                                                 
                                     print("ERROR: Script timeout exceeded!")                                      
                                     sys.exit(1)</parameter>                                                       
                               <parameter=new_str>def main():                                                      
                                 start_time = time.time()                                                          
                                                                                                                   
                                 # Test case 1: No limit - should work now                                         
                                 print("\nTest 1: Testing with no limit...")                                       
                                 cache = LocalCache()                                                              
                                 cache['a'] = 1                                                                    
                                 cache['b'] = 2                                                                    
                                 cache['c'] = 3                                                                    
                                 print("Success: Added items without error")                                       
                                 print("Cache contents:", dict(cache))                                             
                                                                                                                   
                                 # Test case 2: With limit                                                         
                                 print("\nTest 2: Testin

                    INFO     --- Sample #5 ---

                    INFO     [Dataset1: <function=str_replace_editor>]                                             
                             <parameter=command>view</parameter>                                                   
                             <parameter=path>/testbed/safety/scan/ecosystems/python/dependencies.py</parameter>    
                    

                    INFO     [Dataset2: <function=file_editor>]                                                    
                             <parameter=command>view</parameter>                                                   
                               <parameter=path>/testbed</parameter>                                                
                    

                    INFO     =======================================                                               
                    

In [35]:
import re
import logging
from datasets import load_dataset

# # Setup logger (if you already have a logger, skip or adapt this part)
# logger = logging.getLogger(__name__)
# logger.setLevel(logging.INFO)
# handler = logging.StreamHandler()
# logger.addHandler(handler)

def extract_function_calls(dataset_split, function_name, max_samples=5):
    """
    Finds up to `max_samples` full blocks of:
        <function=function_name> ... </function>
    from the assistant messages in a dataset split.

    Returns:
        calls  : A list of the full matched strings (the entire function call).
        params : A set of all parameter names seen across all matches 
                 (e.g., <parameter=some_name>...).
    """
    # Regex to capture the entire <function=...>...</function> block
    # group(0) = entire match
    pattern = re.compile(
        rf"(<function={function_name}>(?:.*?)</function>)",
        re.DOTALL
    )

    # Regex to capture parameter names within the function call
    # group(1) = parameter name
    param_pattern = re.compile(r"<parameter=([^>]+)>", re.DOTALL)

    calls = []
    all_param_names = set()

    for row in dataset_split:
        for msg in row["messages"]:
            if msg["role"] == "assistant":
                matches = pattern.findall(msg["content"])
                for match in matches:
                    # Collect the entire function call
                    if len(calls) < max_samples:
                        calls.append(match.strip())

                    # Find parameter names within this function call
                    param_names = param_pattern.findall(match)
                    for p in param_names:
                        all_param_names.add(p.strip())

    return calls, all_param_names

# Load the two datasets
# dataset1 = load_dataset("SWE-bench/SWE-smith-trajectories")["train"]
dataset1 = ds_out['train']
dataset2 = load_dataset("R2E-Gym/R2EGym-SFT-Trajectories")["train"]

# Each entry is (function_in_dataset1, function_in_dataset2)
pairs_to_compare = [
    ("submit", "finish"),
    ("bash", "execute_bash"),
    ("str_replace_editor", "file_editor")
]

pairs_to_compare = [
    ("finish", "finish"),
    ("execute_bash", "execute_bash"),
    ("file_editor", "file_editor")
]

for fn1, fn2 in pairs_to_compare:
    # Extract calls & parameter sets for function1 in dataset1
    calls1, params1 = extract_function_calls(dataset1, fn1, max_samples=5)
    # Extract calls & parameter sets for function2 in dataset2
    calls2, params2 = extract_function_calls(dataset2, fn2, max_samples=5)

    logger.info(f"=== Comparing '{fn1}' (Dataset1) vs '{fn2}' (Dataset2) ===")
    logger.info(f"Parameters found for '{fn1}' in Dataset1: {params1}")
    logger.info(f"Parameters found for '{fn2}' in Dataset2: {params2}")
    # Show up to 5 side-by-side calls
    max_len = max(len(calls1), len(calls2))
    for i in range(max_len):
        call1 = calls1[i] if i < len(calls1) else "[No more samples]"
        call2 = calls2[i] if i < len(calls2) else "[No more samples]"
        
        logger.info(f"\n--- Sample #{i+1} ---")
        logger.info(f"[Dataset1 <function={fn1}>]:\n{call1}\n")
        logger.info(f"[Dataset2 <function={fn2}>]:\n{call2}\n")

    # Also log the sets of parameter names we found in each dataset
    logger.info(f"Parameters found for '{fn1}' in Dataset1: {params1}")
    logger.info(f"Parameters found for '{fn2}' in Dataset2: {params2}")
    logger.info("=========================================================\n")

[05/05/25 01:14:22] INFO     === Comparing 'finish' (Dataset1) vs 'finish' (Dataset2) ===

                    INFO     Parameters found for 'finish' in Dataset1: {'command'}

                    INFO     Parameters found for 'finish' in Dataset2: {'result', 'command'}

                    INFO                                                                                           
                             --- Sample #1 ---

                    INFO     [Dataset1 <function=finish>]:                                                         
                             <function=finish>                                                                     
                               <parameter=command>submit</parameter>                                               
                             </function>                                                                           
                    

...

                    INFO     [Dataset1 <function=file_editor>]:                                                    
                             <function=file_editor>                                                                
                               <parameter=command>view</parameter>                                                 
                               <parameter=path>/testbed/safety/scan/ecosystems/python/dependencies.py</parameter>  
                             </function>                                                                           
                    

                    INFO     [Dataset2 <function=file_editor>]:                                                    
                             <function=file_editor>                                                                
                               <parameter=command>view</parameter>                                                 
                               <parameter=path>/testbed</parameter>                                                
                             </function>                                                                           
                    

                    INFO     Parameters found for 'file_editor' in Dataset1: {'view_range', 'path', 'new_str',     
                             'old_str', 'insert_line', 'command', 'file_text'}

                    INFO     Parameters found for 'file_editor' in Dataset2: {'search_term', 'new_str', 'path',    
                             'view_range', 'old_str', 'command', 'file_text', 'concise'}

                    INFO     =========================================================                             
                    

In [36]:
import re
import logging
from datasets import load_dataset

# # Setup logger (if you already have a logger, skip or adapt this part)
# logger = logging.getLogger(__name__)
# logger.setLevel(logging.INFO)
# handler = logging.StreamHandler()
# logger.addHandler(handler)

def extract_function_calls(dataset_split, function_name, max_samples=5):
    """
    Finds up to `max_samples` full blocks of:
        <function=function_name> ... </function>
    from assistant messages in a dataset split.

    Also collects parameter names (e.g., <parameter=path>...</parameter>)
    and specifically captures all distinct values for the 'command' parameter.

    Returns:
        calls            : A list of the full matched strings (the entire function call).
        param_names      : A set of parameter names encountered (e.g., {'path', 'command', ...}).
        command_values   : A set of all distinct values for the 'command' parameter.
    """

    # Regex to capture the entire <function=...> ... </function> block
    block_pattern = re.compile(
        rf"(<function={function_name}>(?:.*?)</function>)",
        re.DOTALL
    )
    # Regex to capture parameter=NAME>VALUE</parameter>
    # group(1) = parameter name, group(2) = parameter value
    param_pattern = re.compile(r"<parameter=([^>]+)>(.*?)</parameter>", re.DOTALL)

    calls = []
    param_names = set()
    command_values = set()

    for row in dataset_split:
        for msg in row["messages"]:
            if msg["role"] == "assistant":
                blocks = block_pattern.findall(msg["content"])
                for block in blocks:
                    if len(calls) < max_samples:
                        calls.append(block.strip())

                    # Within this block, extract parameters
                    params = param_pattern.findall(block)
                    for (p_name, p_value) in params:
                        param_names.add(p_name.strip())
                        # If this is the 'command' parameter, store its value
                        if p_name.strip() == "command":
                            # p_value might include newlines; strip them
                            command_values.add(p_value.strip())

    return calls, param_names, command_values

# Load both datasets
dataset1 = load_dataset("SWE-bench/SWE-smith-trajectories")["train"]
dataset2 = load_dataset("R2E-Gym/R2EGym-SFT-Trajectories")["train"]

# We'll compare 'str_replace_editor' (dataset1) vs 'file_editor' (dataset2)
fn1 = "str_replace_editor"
fn2 = "file_editor"

# Extract from Dataset1
calls1, params1, commands1 = extract_function_calls(dataset1, fn1, max_samples=5)
# Extract from Dataset2
calls2, params2, commands2 = extract_function_calls(dataset2, fn2, max_samples=5)

logger.info(f"=== Comparing '{fn1}' (Dataset1) vs '{fn2}' (Dataset2) ===")

# Show up to 5 side-by-side calls
max_len = max(len(calls1), len(calls2))
for i in range(max_len):
    call1 = calls1[i] if i < len(calls1) else "[No more samples]"
    call2 = calls2[i] if i < len(calls2) else "[No more samples]"
    
    logger.info(f"\n--- Sample #{i+1} ---")
    logger.info(f"[Dataset1 <function={fn1}>]:\n{call1}\n")
    logger.info(f"[Dataset2 <function={fn2}>]:\n{call2}\n")

# Also log the parameter sets and command values found
logger.info(f"\nParameters found for '{fn1}' in Dataset1: {params1}")
logger.info(f"Parameters found for '{fn2}' in Dataset2: {params2}")

logger.info(f"\nAll distinct 'command' values for '{fn1}' in Dataset1: {commands1}")
logger.info(f"All distinct 'command' values for '{fn2}' in Dataset2: {commands2}")
logger.info("=========================================================\n")

[05/05/25 01:15:34] INFO     === Comparing 'str_replace_editor' (Dataset1) vs 'file_editor' (Dataset2) ===

                    INFO                                                                                           
                             --- Sample #1 ---

                    INFO     [Dataset1 <function=str_replace_editor>]:                                             
                             <function=str_replace_editor>                                                         
                             <parameter=command>view</parameter>                                                   
                             <parameter=path>/testbed/conan/tools/files/files.py</parameter>                       
                             </function>                                                                           
                    

                    INFO     [Dataset2 <function=file_editor>]:                                                    
                             <function=file_editor>                                                                
                               <parameter=command>view</parameter>                                                 
                               <parameter=path>/testbed/scrapy/utils/datatypes.py</parameter>                      
                             </function>                                                                           
                    

                    INFO                                                                                           
                             --- Sample #2 ---

...

                    INFO                                                                                           
                             Parameters found for 'str_replace_editor' in Dataset1: {'view_range', 'path',         
                             'new_str', 'old_str', 'insert_line', 'command', 'file_text'}

                    INFO     Parameters found for 'file_editor' in Dataset2: {'search_term', 'new_str', 'path',    
                             'view_range', 'old_str', 'command', 'file_text', 'concise'}

                    INFO                                                                                           
                             All distinct 'command' values for 'str_replace_editor' in Dataset1: {'create', 'view',
                             'insert', 'undo_edit', 'str_replace', 'str_replace_editor'}

                    INFO     All distinct 'command' values for 'file_editor' in Dataset2: {'search">\n<parameter   
                             name="search_term">def rename_categories', 'create', 'view', 'str_replace'}

                    INFO     =========================================================                             
                    

In [59]:
import re
from datasets import load_dataset

# Load dataset 1
dataset1 = load_dataset("SWE-bench/SWE-smith-trajectories")["train"]

# Regex to match entire function-call blocks: <function=XYZ> ... </function>
function_pattern = re.compile(r"(<function=[^>]+>.*?</function>)", re.DOTALL)

# Regex to match parameters: <parameter=NAME>VALUE</parameter>
parameter_pattern = re.compile(r"<parameter=([^>]+)>(.*?)</parameter>", re.DOTALL)

# List to hold all matching blocks
undo_edit_calls = []

for row in dataset1:
    for msg in row["messages"]:
        if msg["role"] == "assistant":
            # Find all <function=...> ... </function> blocks in this message
            function_blocks = function_pattern.findall(msg["content"])
            for block in function_blocks:
                # Find all parameters in this block
                params = parameter_pattern.findall(block)
                # Check if 'command' == 'undo_edit' in any of them
                for (p_name, p_value) in params:
                    if p_name.strip() == "command" and p_value.strip() == "undo_edit":
                        undo_edit_calls.append(block)
                        break  # No need to check other parameters in this block

# Print (or otherwise process) all calls that contain command=undo_edit
for i, call in enumerate(undo_edit_calls, start=1):
    logger.info(f"--- Call #{i} ---")
    logger.info(call)
    # print()

[05/05/25 00:37:19] INFO     --- Call #1 ---

                    INFO     <function=str_replace_editor>                                                         
                             <parameter=command>undo_edit</parameter>                                              
                             <parameter=path>/testbed/dvc/commands/ls/__init__.py</parameter>                      
                             </function>

                    INFO     --- Call #2 ---

                    INFO     <function=str_replace_editor>                                                         
                             <parameter=command>undo_edit</parameter>                                              
                             <parameter=path>/testbed/yamllint/rules/indentation.py</parameter>                    
                             </function>

                    INFO     --- Call #3 ---

                    INFO     <function=str_replace_editor>                                                         
                             <parameter=command>undo_edit</parameter>                                              
                             <parameter=path>/testbed/dask/array/ma.py</parameter>                                 
                             </function>

                    INFO     --- Call #4 ---

                    INFO     <function=str_replace_editor>                                                         
                             <parameter=command>undo_edit</parameter>                                              
                             <parameter=path>/testbed/dask/array/__init__.py</parameter>                           
                             </function>

In [40]:
import re
from datasets import load_dataset

dataset1 = load_dataset("SWE-bench/SWE-smith-trajectories")["train"]

# Regex to capture entire <function=bash> ... </function> block.
bash_block_pattern = re.compile(r"(<function=bash>.*?</function>)", re.DOTALL)

# Regex to capture the "cmd" parameter inside a function block, e.g. <parameter=cmd> ... </parameter>
cmd_pattern = re.compile(r"<parameter=command>(.*?)</parameter>", re.DOTALL)

# We’ll store matches here for printing
bash_cd_calls = []

for row in dataset1:
    for msg in row["messages"]:
        if msg["role"] == "assistant":
            # Find all <function=bash> ... </function> blocks in the content
            blocks = bash_block_pattern.findall(msg["content"])
            for block in blocks:
                # Inside each block, find <parameter=cmd>...</parameter>
                matches = cmd_pattern.findall(block)
                for cmd in matches:
                    # If the command text contains "cd " (case-sensitive), we capture this block
                    if "cd " in cmd:
                        bash_cd_calls.append(block)
                        # If you only want to store unique blocks, 
                        # use a set or check for duplicates before appending.

# Print results
for i, block in enumerate(bash_cd_calls, start=1):
    print(f"--- Bash function #{i} containing 'cd' ---")
    print(block)
    print()

--- Bash function #1 containing 'cd' ---
<function=bash>
<parameter=command>cd /testbed && python reproduce.py</parameter>
</function>

--- Bash function #2 containing 'cd' ---
<function=bash>
<parameter=command>cd /testbed && python reproduce.py</parameter>
</function>

--- Bash function #3 containing 'cd' ---
<function=bash>
<parameter=command>cd /testbed && python reproduce_error.py</parameter>
</function>

--- Bash function #4 containing 'cd' ---
<function=bash>
<parameter=command>cd /testbed && python reproduce_error.py</parameter>
</function>

--- Bash function #5 containing 'cd' ---
<function=bash>
<parameter=command>cd /testbed && python reproduce_error.py</parameter>
</function>

--- Bash function #6 containing 'cd' ---
<function=bash>
<parameter=command>cd /testbed && python reproduce_error.py</parameter>
</function>

--- Bash function #7 containing 'cd' ---
<function=bash>
<parameter=command>cd /testbed && python test_edge_cases.py</parameter>
</function>

--- Bash function 

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



In [14]:
from src.r2e_edits.agenthub.action import Action

In [42]:
pairs_to_compare = [
    ("submit", "finish"),
    ("bash", "execute_bash"),
    ("str_replace_editor", "file_editor")
]

idx = 1
fn1 = pairs_to_compare[idx][0]
fn2 = pairs_to_compare[idx][1]

# Extract calls & parameter sets for function1 in dataset1
calls1, params1, _ = extract_function_calls(dataset1, fn1, max_samples=5)
# Extract calls & parameter sets for function2 in dataset2
calls2, params2, _ = extract_function_calls(dataset2, fn2, max_samples=5)

In [44]:
tool_call = calls1[0]
action = Action.from_string(tool_call)
logger.info(action.to_xml_string())
logger.info(f"{action.function_name}, {action.parameters}")
logger.info(f"{action.to_bashcmd()}")

tool_call = calls1[0]
action = Action.from_swesmith_xml_string(xml_str = tool_call)
logger.info(action.to_xml_string())
logger.info(f"{action.function_name}, {action.parameters}")
logger.info(f"{action.to_bashcmd()}")


tool_call = calls2[0]
action = Action.from_string(tool_call)
logger.info(action.to_xml_string())
logger.info(f"{action.function_name}, {action.parameters}")
logger.info(f"{action.to_bashcmd()}")


[05/05/25 01:33:05] INFO     <function=bash>                                                                       
                               <parameter=command>find /testbed -type f -name "*.py" | grep -v "test_"</parameter> 
                             </function>

                    INFO     bash, {'command': 'find /testbed -type f -name "*.py" | grep -v "test_"'}

                    INFO     bash 'find /testbed -type f -name "*.py" | grep -v "test_"'

                    INFO     <function=execute_bash>                                                               
                               <parameter=cmd>find /testbed -type f -name "*.py" | grep -v "test_"</parameter>     
                             </function>

                    INFO     execute_bash, {'cmd': 'find /testbed -type f -name "*.py" | grep -v "test_"'}

                    INFO     execute_bash --cmd 'find /testbed -type f -name "*.py" | grep -v "test_"'

                    INFO     <function=execute_bash>                                                               
                               <parameter=cmd>python /testbed/reproduce_issue.py</parameter>                       
                             </function>

                    INFO     execute_bash, {'cmd': 'python /testbed/reproduce_issue.py'}

                    INFO     execute_bash --cmd 'python /testbed/reproduce_issue.py'

In [32]:
import re
from datasets import load_dataset, DatasetDict
from src.r2e_edits.agenthub.action import Action  # Import your custom Action class

# Regex to match each <function=XYZ>...</function> block
FUNCTION_BLOCK_PATTERN = re.compile(r"(<function=[^>]+>.*?</function>)", re.DOTALL)

def convert_swesmith_to_r2e_gym(text):
    """
    Given one message's text, finds all <function=...>...</function> blocks,
    parses them using Action.from_swesmith_xml_string,
    and replaces them with the new dataset2 format.

    Returns the updated text.
    """
    # Find all function blocks
    blocks = FUNCTION_BLOCK_PATTERN.findall(text)

    # For each block, we parse + convert
    new_text = text
    for block in blocks:
        # Create an Action object, parse from SWE-Smith style
        action = Action.from_swesmith_xml_string(block)
        # action.from_swesmith_xml_string(block)
        
        # Convert to new (R2E-Gym) style
        converted_block = action.to_xml_string()  # e.g. <function=execute_bash>...<parameter=command>... etc.

        # Replace old block with new block in the message
        new_text = new_text.replace(block, converted_block, 1)

    return new_text

def convert_ds():
    # 1) Load the original dataset
    ds_original = load_dataset("SWE-bench/SWE-smith-trajectories")
    
    # 2) Define a function to apply to each row
    def transform_example(example):
        # We'll create a new "messages" array with the assistant messages converted
        new_messages = []
        for msg in example["messages"]:
            if msg["role"] == "assistant":
                # Convert the entire content from SWE-Smith style to R2E-Gym
                new_content = convert_swesmith_to_r2e_gym(msg["content"])
                new_messages.append({"role": msg["role"], "content": new_content})
            else:
                # For user/system messages, leave them as-is
                new_messages.append(msg)

        # Return the updated row
        return {"messages": new_messages}

    # 3) Use `.map(...)` to apply the conversion to each split
    # ds_original is typically a DatasetDict with keys like "train", "validation", etc.
    ds_converted = DatasetDict()
    for split_name, split_data in ds_original.items():
        ds_converted[split_name] = split_data.map(transform_example, batched=False)
    return ds_converted

In [31]:
ds_out = convert_ds()

In [37]:
ds_out

DatasetDict({
    train: Dataset({
        features: ['messages', 'instance_id'],
        num_rows: 5016
    })
})

In [38]:
ds_out.push_to_hub("r2e-edits/SWE-smith-trajectories-R2E")

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Creating parquet from Arrow format:   0%|          | 0/6 [00:00<?, ?ba/s]

CommitInfo(commit_url='https://huggingface.co/datasets/r2e-edits/SWE-smith-trajectories-R2E/commit/e72cfea8500c5af24010e3fced517872034464c7', commit_message='Upload dataset', commit_description='', oid='e72cfea8500c5af24010e3fced517872034464c7', pr_url=None, repo_url=RepoUrl('https://huggingface.co/datasets/r2e-edits/SWE-smith-trajectories-R2E', endpoint='https://huggingface.co', repo_type='dataset', repo_id='r2e-edits/SWE-smith-trajectories-R2E'), pr_revision=None, pr_num=None)

In [47]:
calls1

['<function=str_replace_editor>\n<parameter=command>view</parameter>\n<parameter=path>/testbed/conan/tools/files/files.py</parameter>\n</function>',
 '<function=str_replace_editor>\n<parameter=command>view</parameter>\n<parameter=path>/testbed/conan/tools/files/files.py</parameter>\n<parameter=view_range>[432, 455]</parameter>\n</function>',
 '<function=str_replace_editor>\n<parameter=command>create</parameter>\n<parameter=path>/testbed/reproduce.py</parameter>\n<parameter=file_text>\nfrom conan.tools.files import replace_in_file\n\nclass MockOutput:\n    def warning(self, msg):\n        print("WARNING:", msg)\n\nclass MockConanfile:\n    def __init__(self):\n        self.output = MockOutput()\n\n# Create a test file\nwith open("test.txt", "w") as f:\n    f.write("Hello World!")\n\nconanfile = MockConanfile()\n\n# Test case 1: Pattern not found (should return False)\nresult1 = replace_in_file(conanfile, "test.txt", "Pattern", "Replace", strict=False)\nprint("Pattern not found result:",